In [2]:
%matplotlib inline

import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import psycopg2 as pg
import geopandas as gpd
import mplleaflet
import folium
import json

# get password from .pgpass
connection = pg.connect(database="refinery", user="refinery", host="localhost", port="54321")
trips_connection = pg.connect(database="trips", user="trips", host="localhost", port="54321")


In [3]:
start_analysis = pd.Timestamp(2018, 4, 10, 13, 0)

## Read trip data

In [4]:
sql = """
    select trips.id as id, 
        registry_id, 
        start_time, 
        completed, 
        max(time) as last_point_time, count(*) as num_points, 
        ST_SetSRID(ST_MakeLine(point::geometry order by time asc), 4326) as path,
        trips.updated_at
    from trips join trip_points on trips.id = trip_points.trip_id
    where trips.created_at > %s
    group by trips.id, registry_id, start_time, completed
    having count(*) > 1
    order by registry_id, start_time
"""
df = gpd.GeoDataFrame.from_postgis(sql, trips_connection, geom_col='path', index_col='id', params=[start_analysis] )
df.head()

registry_id          start_time  completed  \
id                                                                          
9217  0d15799e-9948-4e49-b25a-5809db81065f 2018-04-10 13:49:08      False   
9221  0d15799e-9948-4e49-b25a-5809db81065f 2018-04-10 14:29:32      False   
9259  0d15799e-9948-4e49-b25a-5809db81065f 2018-04-10 22:36:07      False   
9267  0d15799e-9948-4e49-b25a-5809db81065f 2018-04-11 06:19:14      False   
9268  0d15799e-9948-4e49-b25a-5809db81065f 2018-04-11 06:28:32      False   

         last_point_time  num_points  \
id                                     
9217 2018-04-10 13:57:52          60   
9221 2018-04-10 20:52:00        2888   
9259 2018-04-10 22:38:53          31   
9267 2018-04-11 06:23:09          10   
9268 2018-04-11 06:38:37          58   

                                                   path  \
id                                                        
9217  LINESTRING (-0.357945 39.4614516, -0.3583016 3...   
9221  LINESTRING (-0.366605 39.4770133, -0.3665683 3...   
9259  LINESTRING (-1.984065 43.306945, -1.9851683 43...   
9267  LINESTRING (-1.9957033 43.3113366, -1.9956766 ...   
9268  LINESTRING (-1.99552 43.3115733, -1.9955333 43...   

                     updated_at  
id                               
9217 2018-04-10 13:57:54.405124  
9221 2018-04-10 20:52:02.012929  
9259 2018-04-10 22:38:54.442371  
9267 2018-04-11 06:23:11.609666  
9268 2018-04-11 06:38:38.982264

In [5]:
import matplotlib.colors

mapa = folium.Map(tiles='cartodbpositron')

registry_ids = df.registry_id.unique()
registry_id_index = dict(zip(registry_ids, range(len(registry_ids))))
color_list = plt.cm.Paired(np.linspace(0, 1, len(registry_ids)))

# add trips
fg=folium.FeatureGroup(name="trips")
for index, trip in df.iterrows():
    gen = ([point[1], point[0]] for point in trip.path.coords)
    color_index = registry_id_index[trip.registry_id]
    color = matplotlib.colors.to_hex(color_list[color_index])
    line = folium.features.PolyLine(list(gen), popup='Vehicle %s<br/>Trip Id: %d' % (trip.registry_id, index), color=color)
    fg.add_child(line)

mapa.add_child(fg)
mapa.fit_bounds(mapa.get_bounds())
mapa

In [6]:
df.groupby('registry_id').agg({'path': 'count'})

path
registry_id                               
0d15799e-9948-4e49-b25a-5809db81065f     5
1dd54cc0-c4dd-4805-9b21-b0210ef4663e     2
2b4eb1a3-60bc-4b47-8c58-65e8f91b0a49     6
47bf0f92-e47e-4da3-87cb-642f037d6a3b     4
69e31cde-bb6d-44c7-b98d-613a30b17623     3
8c0248c9-74e2-437c-a2e3-0c4643cea3e3     3
90a5e332-a273-4fb4-9044-e013f861c03a     5
94502fdf-1515-41fc-bdcd-b3c784ca6570     5
9c666ed2-88bf-4338-81b0-acf43d32ccbe     1
a33647fc-f400-4017-8fa0-eaa0b62b1e15     4
b81a86ae-dc7a-447f-aeac-705ea3e635a0     4
c62e0b3b-0378-4583-9cb3-56f88f3c2785     3
d2144e6a-9379-41ba-9214-b0effb7be5f0     7
e6b8467d-425c-405a-93a3-b13e6c919198     4
fb8a221b-0927-462d-8fbb-be084f5ba37d     3

### Analysis on single vehicle

In [8]:
# vehicle_id='c62e0b3b-0378-4583-9cb3-56f88f3c2785'
vehicle_id='e6b8467d-425c-405a-93a3-b13e6c919198'

In [9]:
vehicle_trips = df[df.registry_id == vehicle_id]
vehicle_trips.head()

registry_id          start_time  completed  \
id                                                                          
9228  e6b8467d-425c-405a-93a3-b13e6c919198 2018-04-10 16:04:14      False   
9229  e6b8467d-425c-405a-93a3-b13e6c919198 2018-04-10 16:31:07      False   
9238  e6b8467d-425c-405a-93a3-b13e6c919198 2018-04-10 18:23:33      False   
9260  e6b8467d-425c-405a-93a3-b13e6c919198 2018-04-11 04:07:39      False   

         last_point_time  num_points  \
id                                     
9228 2018-04-10 16:20:13         148   
9229 2018-04-10 17:05:08         201   
9238 2018-04-10 19:05:19         345   
9260 2018-04-11 04:56:36         408   

                                                   path  \
id                                                        
9228  LINESTRING (-3.6677433 40.41128, -3.667765 40....   
9229  LINESTRING (-3.6784833 40.48554, -3.678455 40....   
9238  LINESTRING (-3.6790066 40.4397783, -3.679175 4...   
9260  LINESTRING (-3.439055 40.2997933, -3.439295 40...   

                     updated_at  
id                               
9228 2018-04-10 16:20:15.257095  
9229 2018-04-10 17:05:09.012656  
9238 2018-04-10 19:05:19.850982  
9260 2018-04-11 04:56:36.771470

## Raw GPS data

In [11]:
sql = """
    select 	gpsd.id,
            registry_id, 
    		st_makepoint((data->>'longitude')::double precision, (data->>'latitude')::double precision) as point, 
    		timestamp, 
    		gpsd.created_at,
    		gpsd.created_at - lag(gpsd.created_at) over w as created_time_elapsed,
    		timestamp - lag(timestamp) over w as time_elapsed
    from gps_data_streams gpss join gps_data gpsd on gpss.id = gpsd.gps_data_stream_id
    where timestamp > %s
    window w as (partition by registry_id order by timestamp)
"""
gps_data = gpd.GeoDataFrame.from_postgis(sql, connection, geom_col='point', index_col='id', params=[start_analysis])
gps_data.head()


registry_id                         point  \
id                                                                           
927869  0d15799e-9948-4e49-b25a-5809db81065f  POINT (-0.357945 39.4614516)   
927870  0d15799e-9948-4e49-b25a-5809db81065f  POINT (-0.3583016 39.462075)   
927872  0d15799e-9948-4e49-b25a-5809db81065f    POINT (-0.3586966 39.4627)   
927873  0d15799e-9948-4e49-b25a-5809db81065f    POINT (-0.358835 39.46294)   
927874  0d15799e-9948-4e49-b25a-5809db81065f   POINT (-0.35884 39.4629283)   

                 timestamp                 created_at created_time_elapsed  \
id                                                                           
927869 2018-04-10 13:49:08 2018-04-10 13:49:09.654090                  NaT   
927870 2018-04-10 13:49:14 2018-04-10 13:49:14.614047      00:00:04.959957   
927872 2018-04-10 13:49:21 2018-04-10 13:49:21.491055      00:00:06.877008   
927873 2018-04-10 13:49:26 2018-04-10 13:49:26.693946      00:00:05.202891   
927874 2018-04-10 13:49:32 2018-04-10 13:49:33.540558      00:00:06.846612   

       time_elapsed  
id                   
927869          NaT  
927870     00:00:06  
927872     00:00:07  
927873     00:00:05  
927874     00:00:06

In [11]:
gps_data[gps_data.registry_id ==vehicle_id].head()

registry_id                          point  \
id                                                                            
926852  8c0248c9-74e2-437c-a2e3-0c4643cea3e3    POINT (-3.67001 40.4096683)   
926856  8c0248c9-74e2-437c-a2e3-0c4643cea3e3     POINT (-3.66991 40.409745)   
926859  8c0248c9-74e2-437c-a2e3-0c4643cea3e3  POINT (-3.6698233 40.4096383)   
926862  8c0248c9-74e2-437c-a2e3-0c4643cea3e3  POINT (-3.6697216 40.4096183)   
926863  8c0248c9-74e2-437c-a2e3-0c4643cea3e3  POINT (-3.6695866 40.4096483)   

                 timestamp                 created_at created_time_elapsed  \
id                                                                           
926852 2018-04-10 12:42:06 2018-04-10 12:42:06.407624                  NaT   
926856 2018-04-10 12:42:12 2018-04-10 12:42:13.392052      00:00:06.984428   
926859 2018-04-10 12:42:18 2018-04-10 12:42:18.672736      00:00:05.280684   
926862 2018-04-10 12:42:24 2018-04-10 12:42:25.364569      00:00:06.691833   
926863 2018-04-10 12:42:30 2018-04-10 12:42:30.466304      00:00:05.101735   

       time_elapsed  
id                   
926852          NaT  
926856     00:00:06  
926859     00:00:06  
926862     00:00:06  
926863     00:00:06

In [12]:
f, ax = plt.subplots(1, figsize=(20,10))
gps_data[gps_data.registry_id == vehicle_id].plot(ax=ax)
df[df.registry_id == vehicle_id].plot(ax=ax, color='red')
mplleaflet.display(fig=f, tiles='cartodb_positron')

In [12]:
f, ax = plt.subplots(1, figsize=(20,10))
gps_data.plot(ax=ax)
mplleaflet.display(fig=f, tiles='cartodb_positron')

## Trip Subset Analysis

In [9]:
tripSubset=[5708, 5709]

mapa = folium.Map(tiles='cartodbpositron')
trips_of_interest = df.loc[tripSubset]
trips_of_interest

registry_id          start_time  completed  \
id                                                                          
5708  ff5fa275-2be0-42ff-a666-abb4af7fa46d 2018-03-19 17:10:12      False   
5709  ff5fa275-2be0-42ff-a666-abb4af7fa46d 2018-03-19 17:27:11      False   

         last_point_time  num_points  \
id                                     
5708 2018-03-19 17:26:39         156   
5709 2018-03-19 18:16:36         411   

                                                   path  \
id                                                        
5708  LINESTRING (-3.8783166 40.0729866, -3.8783166 ...   
5709  LINESTRING (-3.748675 40.2787916, -3.747805 40...   

                     updated_at  
id                               
5708 2018-03-19 17:27:13.897257  
5709 2018-03-19 18:16:36.301615

In [12]:
# add trips

mapa = folium.Map(tiles='cartodbpositron')

fg=folium.FeatureGroup(name="trips")
for index, trip in trips_of_interest.iterrows():
    gen = ([point[1], point[0]] for point in trip.path.coords)
    line = folium.features.PolyLine(list(gen), popup='Trip Id: %d' % index)
    fg.add_child(line)

mapa.add_child(fg)

# add points
gps_in_interval = gps_data[(gps_data.registry_id == vehicle_id) & 
                           (gps_data.timestamp <= trips_of_interest['last_point_time'].max()) &
                           (gps_data.timestamp >= trips_of_interest['start_time'].min())]
for index, row in gps_in_interval.iterrows():
    coords = [row.point.y, row.point.x]
    marker = folium.features.CircleMarker(location=coords, radius=1, popup=str(row.timestamp))
    mapa.add_child(marker)

mapa.fit_bounds(mapa.get_bounds())
mapa



In [106]:
vehicle_trips[['path', 'registry_id']]

path  \
id                                                        
5010  LINESTRING (-3.6677533 40.4113766, -3.6680616 ...   
5016  LINESTRING (-3.6342133 40.5456866, -3.6342016 ...   
5021  LINESTRING (-3.6368433 40.535145, -3.6367783 4...   
5028  LINESTRING (-3.6376416 40.543095, -3.637585 40...   
5031  LINESTRING (-3.6544583 40.493455, -3.654475 40...   
5040  LINESTRING (-3.674275 40.49292, -3.6742433 40....   
5046  LINESTRING (-3.6844283 40.4697266, -3.68657 40...   
5051  LINESTRING (-3.6274383 40.46873, -3.6279516 40...   
5056  LINESTRING (-3.5775683 40.426345, -3.5780383 4...   
5059  LINESTRING (-3.603895 40.4039866, -3.6042583 4...   
5068  LINESTRING (-3.5117416 40.3960883, -3.5094866 ...   
5077  LINESTRING (-3.3831833 40.2607483, -3.3812216 ...   
5082  LINESTRING (-3.1272733 40.094895, -3.125915 40...   
5089  LINESTRING (-2.964145 39.9848133, -2.96315 39....   
5098  LINESTRING (-2.6559066 39.8799033, -2.6538566 ...   
5103  LINESTRING (-2.451515 39.8043183, -2.44939 39....   
5106  LINESTRING (-2.3811083 39.67925, -2.3794516 39...   
5114  LINESTRING (-2.169375 39.4834466, -2.16732 39....   
5122  LINESTRING (-1.9518066 39.5174566, -1.9494233 ...   
5124  LINESTRING (-1.8222333 39.5264233, -1.820185 3...   
5133  LINESTRING (-1.5144983 39.5479733, -1.5144983 ...   

                               registry_id  
id                                          
5010  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5016  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5021  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5028  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5031  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5040  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5046  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5051  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5056  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5059  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5068  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5077  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5082  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5089  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5098  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5103  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5106  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5114  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5122  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5124  9c666ed2-88bf-4338-81b0-acf43d32ccbe  
5133  9c666ed2-88bf-4338-81b0-acf43d32ccbe

## Single Trip analysis

In [60]:
tripId = 5737
trip = df.loc[tripId]
trip

registry_id                     9c666ed2-88bf-4338-81b0-acf43d32ccbe
start_time                                       2018-03-20 05:04:52
completed                                                      False
last_point_time                                  2018-03-20 07:13:15
num_points                                                      1089
path               LINESTRING (-3.705225 40.390035, -3.705245 40....
updated_at                                2018-03-20 07:13:16.626862
Name: 5737, dtype: object

## Event data

In [74]:
sql = """
    select 	ed.id,
            registry_id,
            device_id,
            data->>'startOfTrip' as sot,
            data->>'endOfTrip' as eot,
            data->'endOfTrip'->'totalTime' as trip_time,
    		timestamp
    from event_data_streams eds join event_data ed on eds.id = ed.event_data_stream_id
    where timestamp > %s and (data->>'startOfTrip' is not null or data->>'endOfTrip' is not null)
"""
event_data = pd.read_sql_query(sql, con=connection, index_col='id', params=[start_analysis] )
event_data.head()

registry_id  device_id  \
id                                                       
12772  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   
12783  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   
12793  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   
12805  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   
12860  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   

                                                     sot  \
id                                                         
12772  {"onVoltage": 12.6, "totalTime": 38877, "offVo...   
12783  {"onVoltage": 14.388, "totalTime": 0, "offVolt...   
12793  {"onVoltage": 14.182, "totalTime": 0, "offVolt...   
12805                                               None   
12860  {"onVoltage": 12.433, "totalTime": 7602, "offV...   

                                                     eot  trip_time  \
id                                                                    
12772                                               None        NaN   
12783                                               None        NaN   
12793                                               None        NaN   
12805  {"distance": 3066, "idleTime": 63, "maxSpeed":...      292.0   
12860                                               None        NaN   

                timestamp  
id                         
12772 2018-03-19 19:35:27  
12783 2018-03-19 19:50:30  
12793 2018-03-19 20:00:29  
12805 2018-03-19 20:10:24  
12860 2018-03-19 22:12:11

In [75]:
# estimate start_of_trip
import datetime
eot_data = event_data.loc[event_data.trip_time.dropna().index]
deltas = eot_data.trip_time.apply(lambda x: datetime.timedelta(seconds=x + 300))
eot_data['sot_time'] = eot_data.timestamp - deltas
joined_event_data = event_data.join(eot_data[['sot_time']]).sort_values(by=['registry_id', 'timestamp'])
joined_event_data.head()

registry_id  device_id  \
id                                                       
12750  1dd54cc0-c4dd-4805-9b21-b0210ef4663e        123   
12756  1dd54cc0-c4dd-4805-9b21-b0210ef4663e        123   
12763  1dd54cc0-c4dd-4805-9b21-b0210ef4663e        123   
12770  1dd54cc0-c4dd-4805-9b21-b0210ef4663e        123   
12776  1dd54cc0-c4dd-4805-9b21-b0210ef4663e        123   

                                                     sot  \
id                                                         
12750  {"onVoltage": 12.607, "totalTime": 18504, "off...   
12756  {"onVoltage": 14.158, "totalTime": 0, "offVolt...   
12763  {"onVoltage": 14.213, "totalTime": 0, "offVolt...   
12770  {"onVoltage": 14.225, "totalTime": 0, "offVolt...   
12776                                               None   

                                                     eot  trip_time  \
id                                                                    
12750                                               None        NaN   
12756                                               None        NaN   
12763                                               None        NaN   
12770                                               None        NaN   
12776  {"distance": 3649, "idleTime": 87, "maxSpeed":...      475.0   

                timestamp            sot_time  
id                                             
12750 2018-03-19 18:53:23                 NaT  
12756 2018-03-19 19:11:17                 NaT  
12763 2018-03-19 19:19:08                 NaT  
12770 2018-03-19 19:24:48                 NaT  
12776 2018-03-19 19:37:43 2018-03-19 19:24:48

In [76]:
# trip events
trip_events = joined_event_data[(joined_event_data.registry_id==trip.registry_id) &
                                (joined_event_data.timestamp >= trip.start_time) &
                                (joined_event_data.timestamp <= trip.last_point_time + datetime.timedelta(minutes=6))]
trip_events

registry_id  device_id  \
id                                                       
12868  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12876  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12878  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12882  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12886  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12890  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12892  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12896  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12903  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12909  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12912  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12922  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12925  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
12929  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   

                                                     sot  \
id                                                         
12868  {"onVoltage": 12.495, "totalTime": 26682, "off...   
12876  {"onVoltage": 12.541, "totalTime": 0, "offVolt...   
12878  {"onVoltage": 14.388, "totalTime": 0, "offVolt...   
12882  {"onVoltage": 12.729, "totalTime": 0, "offVolt...   
12886  {"onVoltage": 14.443, "totalTime": 0, "offVolt...   
12890  {"onVoltage": 14.709, "totalTime": 0, "offVolt...   
12892  {"onVoltage": 12.795, "totalTime": 0, "offVolt...   
12896  {"onVoltage": 12.892, "totalTime": 0, "offVolt...   
12903  {"onVoltage": 14.394, "totalTime": 0, "offVolt...   
12909  {"onVoltage": 14.467, "totalTime": 0, "offVolt...   
12912  {"onVoltage": 12.692, "totalTime": 0, "offVolt...   
12922  {"onVoltage": 13.964, "totalTime": 0, "offVolt...   
12925  {"onVoltage": 14.358, "totalTime": 0, "offVolt...   
12929                                               None   

                                                     eot  trip_time  \
id                                                                    
12868                                               None        NaN   
12876                                               None        NaN   
12878                                               None        NaN   
12882                                               None        NaN   
12886                                               None        NaN   
12890                                               None        NaN   
12892                                               None        NaN   
12896                                               None        NaN   
12903                                               None        NaN   
12909                                               None        NaN   
12912                                               None        NaN   
12922                                               None        NaN   
12925                                               None        NaN   
12929  {"distance": 3659, "idleTime": 25, "maxSpeed":...      202.0   

                timestamp            sot_time  
id                                             
12868 2018-03-20 05:04:52                 NaT  
12876 2018-03-20 05:22:03                 NaT  
12878 2018-03-20 05:34:17                 NaT  
12882 2018-03-20 05:36:14                 NaT  
12886 2018-03-20 05:44:05                 NaT  
12890 2018-03-20 05:50:27                 NaT  
12892 2018-03-20 05:52:24                 NaT  
12896 2018-03-20 06:04:37                 NaT  
12903 2018-03-20 06:25:41                 NaT  
12909 2018-03-20 06:35:44                 NaT  
12912 2018-03-20 06:45:46                 NaT  
12922 2018-03-20 07:00:12                 NaT  
12925 2018-03-20 07:10:14                 NaT  
12929 2018-03-20 07:18:41 2018-03-20 07:10:19

In [69]:
event_id = 12962
json.loads(joined_event_data.loc[event_id].sot)

{'offVoltage': 0.0, 'onVoltage': 14.425, 'totalTime': 0}

In [49]:
eot_data[eot_data.registry_id == trip.registry_id]

registry_id   sot  \
id                                                  
12766  69e31cde-bb6d-44c7-b98d-613a30b17623  None   
12775  69e31cde-bb6d-44c7-b98d-613a30b17623  None   
12811  69e31cde-bb6d-44c7-b98d-613a30b17623  None   
12821  69e31cde-bb6d-44c7-b98d-613a30b17623  None   

                                                     eot  trip_time  \
id                                                                    
12766  {"distance": 15, "idleTime": 15, "maxSpeed": 7...       32.0   
12775  {"distance": 1, "idleTime": 53, "maxSpeed": 2,...       57.0   
12811  {"distance": 0, "idleTime": 43, "maxSpeed": 0,...       43.0   
12821  {"distance": 0, "idleTime": 287, "maxSpeed": 0...      287.0   

                timestamp            sot_time  
id                                             
12766 2018-03-19 19:23:51 2018-03-19 19:18:19  
12775 2018-03-19 19:31:34 2018-03-19 19:25:37  
12811 2018-03-19 20:18:31 2018-03-19 20:12:48  
12821 2018-03-19 20:33:01 2018-03-19 20:23:14

## Intermediate Trip Analysis

In [82]:
sql = """
    select *, to_timestamp((data->>'ts')::bigint/1000) as timestamp
    from data_feeds
    where created_at >= %s and 
        data->'values'->'obdIt' is not null
"""
it_data = pd.read_sql_query(sql, con=connection, index_col='id', params=[start_analysis] )
it_data.head()

data  retries  \
id                                                                    
1467581  {'ts': 1521482403438, 'imei': '861508034373357...        0   
1467582  {'ts': 1521482409260, 'imei': '861508034373357...        0   
1467583  {'ts': 1521482415290, 'imei': '861508034373357...        0   
1467584  {'ts': 1521482420647, 'imei': '861508034373357...        0   
1467585  {'ts': 1521482426434, 'imei': '861508034373357...        0   

                        created_at                 updated_at  \
id                                                              
1467581 2018-03-19 18:00:03.823002 2018-03-19 18:00:03.823002   
1467582 2018-03-19 18:00:10.696600 2018-03-19 18:00:10.696600   
1467583 2018-03-19 18:00:15.553891 2018-03-19 18:00:15.553891   
1467584 2018-03-19 18:00:21.019094 2018-03-19 18:00:21.019094   
1467585 2018-03-19 18:00:27.701103 2018-03-19 18:00:27.701103   

                                  registry_id  device_id  \
id                                                         
1467581  ff5fa275-2be0-42ff-a666-abb4af7fa46d          5   
1467582  ff5fa275-2be0-42ff-a666-abb4af7fa46d          5   
1467583  ff5fa275-2be0-42ff-a666-abb4af7fa46d          5   
1467584  ff5fa275-2be0-42ff-a666-abb4af7fa46d          5   
1467585  ff5fa275-2be0-42ff-a666-abb4af7fa46d          5   

                        timestamp  
id                                 
1467581 2018-03-19 18:00:03+00:00  
1467582 2018-03-19 18:00:09+00:00  
1467583 2018-03-19 18:00:15+00:00  
1467584 2018-03-19 18:00:20+00:00  
1467585 2018-03-19 18:00:26+00:00

In [86]:
event_data_by_timestamp = event_data[['registry_id', 'device_id', 'sot', 'eot', 'timestamp']].set_index('timestamp')
it_data_by_timestamp = it_data[['registry_id', 'device_id', 'timestamp', 'data']].set_index('timestamp')
all_events = event_data_by_timestamp.append(it_data_by_timestamp)
all_events.rename(columns = {'data':'it'}, inplace = True)
all_events = all_events[['registry_id', 'device_id', 'sot', 'it', 'eot']]
all_events.head()

registry_id  device_id  \
timestamp                                                              
2018-03-19 19:35:27  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   
2018-03-19 19:50:30  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   
2018-03-19 20:00:29  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   
2018-03-19 20:10:24  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   
2018-03-19 22:12:11  94502fdf-1515-41fc-bdcd-b3c784ca6570          9   

                                                                   sot   it  \
timestamp                                                                     
2018-03-19 19:35:27  {"onVoltage": 12.6, "totalTime": 38877, "offVo...  NaN   
2018-03-19 19:50:30  {"onVoltage": 14.388, "totalTime": 0, "offVolt...  NaN   
2018-03-19 20:00:29  {"onVoltage": 14.182, "totalTime": 0, "offVolt...  NaN   
2018-03-19 20:10:24                                               None  NaN   
2018-03-19 22:12:11  {"onVoltage": 12.433, "totalTime": 7602, "offV...  NaN   

                                                                   eot  
timestamp                                                               
2018-03-19 19:35:27                                               None  
2018-03-19 19:50:30                                               None  
2018-03-19 20:00:29                                               None  
2018-03-19 20:10:24  {"distance": 3066, "idleTime": 63, "maxSpeed":...  
2018-03-19 22:12:11                                               None

In [164]:
all_trip_events = all_events[all_events.registry_id==trip.registry_id]
all_trip_events.index = pd.to_datetime(all_trip_events.index)
all_trip_events = all_trip_events.loc[(all_trip_events.index >= trip.start_time.tz_localize('UTC')) &
                                      (all_trip_events.index <= trip.last_point_time.tz_localize('UTC') + datetime.timedelta(minutes=6))]
all_trip_events.head()

registry_id  device_id  \
timestamp                                                                    
2018-03-20 05:04:52+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:22:03+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:34:17+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:36:14+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:44:05+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   

                                                                         sot  \
timestamp                                                                      
2018-03-20 05:04:52+00:00  {"onVoltage": 12.495, "totalTime": 26682, "off...   
2018-03-20 05:22:03+00:00  {"onVoltage": 12.541, "totalTime": 0, "offVolt...   
2018-03-20 05:34:17+00:00  {"onVoltage": 14.388, "totalTime": 0, "offVolt...   
2018-03-20 05:36:14+00:00  {"onVoltage": 12.729, "totalTime": 0, "offVolt...   
2018-03-20 05:44:05+00:00  {"onVoltage": 14.443, "totalTime": 0, "offVolt...   

                            it   eot  
timestamp                             
2018-03-20 05:04:52+00:00  NaN  None  
2018-03-20 05:22:03+00:00  NaN  None  
2018-03-20 05:34:17+00:00  NaN  None  
2018-03-20 05:36:14+00:00  NaN  None  
2018-03-20 05:44:05+00:00  NaN  None

In [123]:
all_trip_events.it.apply(lambda x: json.loads(x))
all_trip_events.sort_index()

registry_id  device_id  \
timestamp                                                                    
2018-03-20 05:04:52+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:04:52+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:04:55+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:00+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:07+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:12+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:18+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:24+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:29+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:37+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:42+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:43+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:50+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:57+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:01+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:06+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:14+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:18+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:24+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:30+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:36+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:42+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:48+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:54+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:00+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:06+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:12+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:18+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:22+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:29+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
...                                                         ...        ...   
2018-03-20 07:10:49+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:10:55+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:04+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:09+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:15+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:19+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:26+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:32+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:38+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:47+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:49+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:11:56+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:12:01+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:12:09+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:12:14+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:12:21+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:12:26+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:12:31+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 07:12:39+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14

In [165]:
it_time = all_trip_events.it.dropna().apply(lambda x: x['values']['obdIt']['totalTime'])
it_time = pd.DataFrame(it_time).rename(columns={'it': 'it_total_time'})
all_trip_events = all_trip_events.join(it_time)
all_trip_events.head()

registry_id  device_id  \
timestamp                                                                    
2018-03-20 05:04:52+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:04:52+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:04:55+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:00+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:07+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   

                                                                         sot  \
timestamp                                                                      
2018-03-20 05:04:52+00:00  {"onVoltage": 12.495, "totalTime": 26682, "off...   
2018-03-20 05:04:52+00:00                                                NaN   
2018-03-20 05:04:55+00:00                                                NaN   
2018-03-20 05:05:00+00:00                                                NaN   
2018-03-20 05:05:07+00:00                                                NaN   

                                                                          it  \
timestamp                                                                      
2018-03-20 05:04:52+00:00                                                NaN   
2018-03-20 05:04:52+00:00  {'ts': 1521522292399, 'imei': '861508034383406...   
2018-03-20 05:04:55+00:00  {'ts': 1521522295110, 'imei': '861508034383406...   
2018-03-20 05:05:00+00:00  {'ts': 1521522300740, 'imei': '861508034383406...   
2018-03-20 05:05:07+00:00  {'ts': 1521522307088, 'imei': '861508034383406...   

                            eot  it_total_time  
timestamp                                       
2018-03-20 05:04:52+00:00  None            7.0  
2018-03-20 05:04:52+00:00   NaN            7.0  
2018-03-20 05:04:55+00:00   NaN           12.0  
2018-03-20 05:05:00+00:00   NaN           19.0  
2018-03-20 05:05:07+00:00   NaN           25.0

In [169]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(all_trip_events.sort_index())

registry_id  device_id  \
timestamp                                                                    
2018-03-20 05:04:52+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:04:52+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:04:55+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:00+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:07+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:12+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:18+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:24+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:29+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:37+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:42+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:43+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:50+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:05:57+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:01+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:06+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:14+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:18+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:24+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:30+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:36+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:42+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:48+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:06:54+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:00+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:06+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:12+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:18+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:22+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:29+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:36+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:43+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:48+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:07:54+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:00+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:06+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:12+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:18+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:25+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:29+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:36+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:47+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:48+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:08:54+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:09:00+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:09:06+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:09:14+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:09:18+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:09:25+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14   
2018-03-20 05:09:30+00:00  9c666ed2-88bf-4338-81b0-acf43d32ccbe         14